In [ ]:
import pandas as pd
import numpy as np
import itertools
import datetime
import exploration.dispersion as disp
import matplotlib.pyplot as plt
import statsmodels.formula.api as smf
import analytics.tranche_data as tdata

from analytics.basket_index import MarkitBasketIndex
from analytics import on_the_run
from statsmodels.graphics.regressionplots import plot_fit
from pygam import LinearGAM, s, f, GAM
from utils.db import dbengine

serenitas_engine = dbengine('serenitasdb')

In [ ]:
%matplotlib inline

In [ ]:
value_date = (datetime.datetime.today() - pd.offsets.BDay(1)).date()
start_date = datetime.date(2019,9,27)
end_date = datetime.date(2020,1,30)
index_type = 'HY'

In [ ]:
#Get Gini factor
date_range = pd.bdate_range(end=value_date, freq='5B',periods=52*4)
risk = disp.get_tranche_data(index_type, serenitas_engine)
risk = risk[risk.index.get_level_values(0).isin(date_range)]
gini_model, gini_calc = disp.create_models(risk, use_gini=True, use_log=True)

In [ ]:
#Plot Gini if (use gini=True, use_log=False)
to_plot_gini = gini_calc.xs(0, level='attach').groupby(['date', 'series']).nth(-1)
to_plot_gini['dispersion'].unstack().plot()

In [ ]:
#Today's mispricing
today = gini_calc.xs([value_date,33], level=['date','series'])
today[['exp_percentage', 'predict_N', 'predict_preN', 'mispricing']]

In [ ]:
#plot mispricing of a tranche through time 
attach = 0
to_plot = gini_calc.xs(attach, level='attach')['mispricing']
to_plot.reset_index(['index','tenor'], drop=True).unstack().plot()

In [ ]:
#plot mispricing of series through time 
series = 33
to_plot = gini_calc.xs(series, level='series')['mispricing']
to_plot.reset_index(['index','tenor'], drop=True).unstack().plot()

In [ ]:
plot_fit(gini_model[0], 'np.log(index_duration)')

In [ ]:
gini_calc.to_csv('/home/serenitas/edwin/Python/' + index_type+ '_tranche_model.csv')

In [ ]:
#compare to realized delta-adjusted return
tranche_returns = tdata.get_tranche_quotes(index=index_type)
tranche_returns = tdata.tranche_returns(df=tranche_returns)
attach = 0
t = tranche_returns['deladj_return'].reset_index(['index', 'tenor'], drop=True).xs(attach, level='attach')
temp={}
for i,g in t.groupby('series'):
    temp[i] = (g.dropna()+1).cumprod()
t = pd.concat(temp).reset_index(0, drop=True)
t.unstack(level='series').plot()

In [ ]:
#compare models
a = [True, False]
for years in [1,2,3,4,5,6]:
    date_range = pd.bdate_range(end=value_date, freq='5B',periods=52*years)
    risk = disp.get_tranche_data(index_type, serenitas_engine)
    risk = risk[risk.index.get_level_values(0).isin(date_range)]
    for x, y in list(itertools.product(a,a)):
        gini_model, gini_calc = disp.create_models(risk, use_gini=x, use_log=y)
        for i, m in gini_model.items():
            print (years, x, y, i, m.rsquared)
        today = gini_calc.xs([value_date,33], level=['date','series'])
        print (today[['exp_percentage', 'predict_N', 'predict_preN', 'mispricing']])

In [ ]:
#Run a particular gini scenario
scenario = gini_calc.loc(axis=0)[value_date,33,'HY','5yr',0]
scenario['dispersion'] = .6
scenario_disp = np.exp(gini_model[0].predict(scenario))
mispricing = (scenario['exp_percentage'] - scenario_disp) * \
             scenario['index_expected_loss'] / \
             (scenario['detach_adj'] - scenario['attach_adj']) / \
             scenario['indexfactor'] * 10000
mispricing

In [ ]:
gini_calc.loc(axis=0)[:,33,'HY','5yr',0]['mispricing']

In [ ]:
#Let's use a GAM model instead?
#only use the 5yr point for modeling
equity = gini_calc.loc(axis=0)[:,:,[25,27,29,31,33],'5yr',0]
X = np.array(equity[['gini_spread', 'duration', 'moneyness']])
y = np.array(equity['exp_percentage'])

#Fit for Lamda
gam_model = GAM(s(0, n_splines=5) +
                  s(1, n_splines=5) +
                  s(2, n_splines=5))
lam = np.logspace(-3, 5, 5, base=3)
lams = [lam] * 3
gam_model.gridsearch(X, y, lam=lams)

gam_model.summary()

In [ ]:
## plotting
fig, axs = plt.subplots(1,3);

titles = ['gini_spread', 'duration', 'moneyness']
for i, ax in enumerate(axs):
    XX = gam_model.generate_X_grid(term=i)
    ax.plot(XX[:, i], gam_model.partial_dependence(term=i, X=XX))
    ax.plot(XX[:, i], gam_model.partial_dependence(term=i, X=XX, width=.95)[1], c='r', ls='--')
    if i == 0:
        ax.set_ylim(-30,30)
    ax.set_title(titles[i]);

In [ ]:
plt.scatter(y, gam_model.predict(X))
plt.xlabel('actual correlation')
plt.ylabel('predicted correlation')

In [ ]:
today = gini_calc.loc(axis=0)[value_date,'HY',33,'5yr',0]
predict_HY33 = gam_model.predict(np.array(today[['gini_spread', 'duration', 'moneyness']]))

In [ ]:
today, predict_HY33